SARIMAX (Seasonal AutoRegressive Integrated Moving Average with eXogenous factors) 
Inputs for oder and seasonaility order affect the models cability - We took a range of common hyperparmater values and trained a mode

order: The order of the non-seasonal ARIMA components. It consists of three integers (p, d, q):
p: The order of the autoregressive (AR) component, which models the dependency of the current value on past values of the time series.
d: The degree of differencing required to make the time series stationary. It represents the number of times the series needs to be differenced to remove trend and seasonality.
q: The order of the moving average (MA) component, which models the dependency of the current value on past forecast errors.

Seasonal_order: The order of the seasonal ARIMA components. It also consists of three integers (P, D, Q):
P: The order of the seasonal autoregressive (SAR) component.
D: The degree of seasonal differencing.
Q: The order of the seasonal moving average (SMA) component.
s: Periodicity, normally 12 or 4

Set up data

1 - Acutaly sales vs predicted sales for each model
2 - Which model perfoms best
3 - How does that model preform against each family

In [2]:
# BASE
# ------------------------------------------------------
import numpy as np
import pandas as pd
import os
import gc
import warnings
from pathlib import Path
#!pip install xgboost
import sklearn
from sklearn import linear_model
from sklearn.linear_model  import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.datasets import make_regression
import xgboost as xgb
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split, TimeSeriesSplit 
from sklearn.metrics import mean_absolute_error, mean_squared_error, mean_squared_log_error, r2_score
pd.set_option('display.max_colwidth', None)
import statsmodels.api as sm

import numpy as np
from sklearn.model_selection import TimeSeriesSplit
from statsmodels.tsa.statespace.sarimax import SARIMAX


from pandas import datetime
from pandas import read_csv
from pandas import DataFrame
from statsmodels.tsa.arima.model import ARIMA
from matplotlib import pyplot

# DATA VISUALIZATION
# ------------------------------------------------------
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go

# CONFIGURATIONS
# ------------------------------------------------------
pd.set_option('display.max_columns', None)
pd.options.display.float_format = '{:.2f}'.format
warnings.filterwarnings('ignore')
folder = 'C:/Users/eflanag/OneDrive - FTI Consulting/Documents/Projects/Ibex_EF/IbexV2/ibexgit/kaggle-store-sales/data/EF_analysis/'

C:\Users\eflanag\AppData\Local\Temp\ipykernel_26992\2644384237.py:27: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.
  from pandas import datetime


In [3]:
def combine_csvs(folder_path, folder_path1 ):
    # Create an empty DataFrame to store the combined data
    combined_df = pd.DataFrame()

    # Iterate over the files in the folder
    for filename in os.listdir(folder_path):
        if filename.endswith('.csv'):
            file_path = os.path.join(folder_path, filename)
            
            # Read the CSV file into a DataFrame
            df = pd.read_csv(file_path)
            df['feature_status'] = 'Features'
            # Concatenate the current DataFrame with the combined DataFrame
            combined_df = pd.concat([combined_df, df], ignore_index=True)
    

    # Iterate over the files in the folder
    for filename in os.listdir(folder_path1):
        if filename.endswith('.csv'):
            file_path = os.path.join(folder_path1, filename)
            
            # Read the CSV file into a DataFrame
            df = pd.read_csv(file_path)
            df['feature_status'] = 'No Features'
            
            # Concatenate the current DataFrame with the combined DataFrame
            combined_df = pd.concat([combined_df, df], ignore_index=True)

    return combined_df

folder_exog = folder + 'exog/'
folder_no_exog = folder + 'no_exog/'

# Call the function to combine the CSV files
result_df = combine_csvs(folder_exog, folder_no_exog)

# Print the combined DataFrame
result_df['order_and_seasonal_order'] = result_df['feature_status']+' - '+result_df['order'] +''+ result_df['seasonal_order']
result_df['error'] = result_df['y_pred_raw'] - result_df['sales']  


In [4]:

result_df['order'].unique()

array(['[1 0 0]', '[0 1 0]', '[1 0 1]'], dtype=object)

In [5]:

result_df['seasonal_order'].unique()

array(['[1 0 1 12]', '[0 1 1 12]', '[1 0 0 12]'], dtype=object)

In [6]:

result_df['order_and_seasonal_order'].nunique()

18

In [7]:
result_df.head()

Unnamed: 0 test/train  sales  store_nbr        date  month  day_of_month  \
0           0      train  15.00         44  02/08/2017      8             2   
1           1      train  21.00         45  02/08/2017      8             2   
2           2      train  20.00         46  02/08/2017      8             2   
3           3      train  14.00         47  02/08/2017      8             2   
4           4      train  15.00         48  02/08/2017      8             2   

   week_of_year  day_of_week  dcoilwtico_interpolated  family_encoded  \
0            31            3                    49.28               0   
1            31            3                    49.28               0   
2            31            3                    49.28               0   
3            31            3                    49.28               0   
4            31            3                    49.28               0   

   type_encoded  y_pred  y_pred_raw    order seasonal_order  fit_time  \
0             0      11       11.00  [1 0 0]     [1 0 1 12]       514   
1             0      11       11.00  [1 0 0]     [1 0 1 12]       514   
2             0      10       10.00  [1 0 0]     [1 0 1 12]       514   
3             0      12       12.00  [1 0 0]     [1 0 1 12]       514   
4             0      11       11.00  [1 0 0]     [1 0 1 12]       514   

  feature_status      order_and_seasonal_order  error  
0       Features  Features - [1 0 0][1 0 1 12]  -4.00  
1       Features  Features - [1 0 0][1 0 1 12] -10.00  
2       Features  Features - [1 0 0][1 0 1 12] -10.00  
3       Features  Features - [1 0 0][1 0 1 12]  -2.00  
4       Features  Features - [1 0 0][1 0 1 12]  -4.00

In [8]:

# Group the data by 'date' and 'order_and_seasonal_order' and calculate the sum of 'sales' and 'y_pred'
grouped_df = result_df.groupby(['date', 'order_and_seasonal_order']).sum().reset_index()
grouped_df['features'] = grouped_df['order_and_seasonal_order'].apply(lambda x: 0 if 'No' in x else 1)

# Plot the grouped data using Plotly
fig = px.line(grouped_df, x='date', y='y_pred_raw', color='order_and_seasonal_order',  symbol='features', symbol_map={1: 'square', 0: 'star'})

# Add a separate line plot for 'sales' with a thicker line and different color
sales_df = grouped_df[['date','sales']]
fig.add_scatter(x=sales_df['date'], y=sales_df['sales'], mode='lines',
                name='Sales', line=dict(color='red', width=3, dash='dash'))

# Add labels and title to the plot
fig.update_layout(
    title="Sum Sales and y_pred over time",
    xaxis_title="Date",
    yaxis_title="Value"
)

# Show the plot
fig.show()


# Group the data by 'date' and 'order_and_seasonal_order' and calculate the sum of 'sales' and 'y_pred'
grouped_df = result_df.groupby(['date', 'order_and_seasonal_order']).mean().reset_index()
grouped_df['features'] = grouped_df['order_and_seasonal_order'].apply(lambda x: 0 if 'No' in x else 1)

# Plot the grouped data using Plotly
fig = px.line(grouped_df, x='date', y='y_pred_raw', color='order_and_seasonal_order',  symbol='features', symbol_map={1: 'square', 0: 'star'})

# Add a separate line plot for 'sales' with a thicker line and different color
sales_df = grouped_df[['date','sales']]
fig.add_scatter(x=sales_df['date'], y=sales_df['sales'], mode='lines',
                name='Sales', line=dict(color='red', width=3, dash='dash'))

# Add labels and title to the plot
fig.update_layout(
    title="Avg Sales and y_pred over time",
    xaxis_title="Date",
    yaxis_title="Value"
)

# Show the plot
fig.show()

In [9]:
grouped_df

date         order_and_seasonal_order  Unnamed: 0  sales  \
0    02/08/2017     Features - [0 1 0][0 1 1 12]    12122.50 541.36   
1    02/08/2017     Features - [0 1 0][1 0 0 12]    12122.50 541.36   
2    02/08/2017     Features - [0 1 0][1 0 1 12]    12122.50 541.36   
3    02/08/2017     Features - [1 0 0][0 1 1 12]    12122.50 541.36   
4    02/08/2017     Features - [1 0 0][1 0 0 12]    12122.50 541.36   
..          ...                              ...         ...    ...   
247  15/08/2017  No Features - [1 0 0][1 0 0 12]    12824.50 427.98   
248  15/08/2017  No Features - [1 0 0][1 0 1 12]    12824.50 427.98   
249  15/08/2017  No Features - [1 0 1][0 1 1 12]    12824.50 427.98   
250  15/08/2017  No Features - [1 0 1][1 0 0 12]    12824.50 427.98   
251  15/08/2017  No Features - [1 0 1][1 0 1 12]    12824.50 427.98   

     store_nbr  month  day_of_month  week_of_year  day_of_week  \
0        27.50   8.00          2.00         31.00         3.00   
1        27.50   8.00          2.00         31.00         3.00   
2        27.50   8.00          2.00         31.00         3.00   
3        27.50   8.00          2.00         31.00         3.00   
4        27.50   8.00          2.00         31.00         3.00   
..         ...    ...           ...           ...          ...   
247      27.50   8.00         15.00         33.00         2.00   
248      27.50   8.00         15.00         33.00         2.00   
249      27.50   8.00         15.00         33.00         2.00   
250      27.50   8.00         15.00         33.00         2.00   
251      27.50   8.00         15.00         33.00         2.00   

     dcoilwtico_interpolated  family_encoded  type_encoded  y_pred  \
0                      49.28           16.00          2.00 1033.52   
1                      49.28           16.00          2.00 1040.65   
2                      49.28           16.00          2.00 1052.74   
3                      49.28           16.00          2.00  521.02   
4                      49.28           16.00          2.00  408.77   
..                       ...             ...           ...     ...   
247                    47.30           16.00          2.00    0.00   
248                    47.30           16.00          2.00  486.53   
249                    47.30           16.00          2.00  359.65   
250                    47.30           16.00          2.00    6.80   
251                    47.30           16.00          2.00   54.12   

     y_pred_raw  fit_time   error  features  
0       1033.52    483.30  492.15         1  
1       1040.65     88.48  499.28         1  
2       1052.74    230.18  511.38         1  
3        521.02    877.88  -20.34         1  
4        408.77    429.94 -132.60         1  
..          ...       ...     ...       ...  
247         NaN     11.70     NaN         0  
248         NaN     63.76     NaN         0  
249         NaN    125.55     NaN         0  
250         NaN     32.45     NaN         0  
251         NaN     88.76     NaN         0  

[252 rows x 17 columns]

In [10]:
import plotly.express as px

# Grouping the DataFrame by family_encoded
grouped_df_family = result_df.groupby(['family_encoded','date']).mean().reset_index()

# Group the data by 'date' and 'order_and_seasonal_order' and calculate the sum of 'sales' and 'y_pred'
#grouped_df = result_df.groupby(['date', 'order_and_seasonal_order']).sum().reset_index()

#grouped_df['features'] = grouped_df['order_and_seasonal_order'].apply(lambda x: 0 if 'No' in x else 1)
grouped_df_family


family_encoded        date  Unnamed: 0  sales  store_nbr  month  \
0                 0  02/08/2017       26.50   7.78      27.50   8.00   
1                 0  03/08/2017       80.50   6.81      27.50   8.00   
2                 0  04/08/2017      134.50   7.76      27.50   8.00   
3                 0  05/08/2017      188.50   9.50      27.50   8.00   
4                 0  06/08/2017      242.50  10.80      27.50   8.00   
..              ...         ...         ...    ...        ...    ...   
457              32  11/08/2017    24704.50  23.57      27.50   8.00   
458              32  12/08/2017    24758.50  19.04      27.50   8.00   
459              32  13/08/2017    24812.50  20.70      27.50   8.00   
460              32  14/08/2017    24866.50  17.98      27.50   8.00   
461              32  15/08/2017    24920.50  17.97      27.50   8.00   

     day_of_month  week_of_year  day_of_week  dcoilwtico_interpolated  \
0            2.00         31.00         3.00                    49.28   
1            3.00         31.00         4.00                    49.40   
2            4.00         31.00         5.00                    49.38   
3            5.00         31.00         6.00                    49.50   
4            6.00         31.00         7.00                    49.44   
..            ...           ...          ...                      ...   
457         11.00         32.00         5.00                    48.60   
458         12.00         32.00         6.00                    48.40   
459         13.00         32.00         7.00                    48.00   
460         14.00         33.00         1.00                    47.72   
461         15.00         33.00         2.00                    47.30   

     type_encoded  y_pred  y_pred_raw  fit_time  error  
0            2.00    6.87        8.41    285.00   0.63  
1            2.00    6.78        8.85    285.00   2.03  
2            2.00    7.05        9.62    285.00   1.86  
3            2.00    7.42       10.42    285.00   0.92  
4            2.00    7.82       11.22    285.00   0.42  
..            ...     ...         ...       ...    ...  
457          2.00   30.62       50.75    179.72  27.18  
458          2.00   31.55       52.59    179.72  33.55  
459          2.00   32.48       54.47    179.72  33.76  
460          2.00   26.73       42.94    179.72  24.97  
461          2.00   27.62       44.73    179.72  26.77  

[462 rows x 15 columns]

Which model perfomred best

In [11]:
result_df_nonan = result_df.dropna()

grouped_df_ = result_df_nonan.groupby(['order_and_seasonal_order']).sum().reset_index()
closest_to_zero_index = grouped_df_['error'].sub(0).abs().idxmin()
closest_to_zero_row = grouped_df.loc[closest_to_zero_index]
closest_to_zero_row = pd.DataFrame(closest_to_zero_row).transpose()
closest_to_zero_row

date      order_and_seasonal_order Unnamed: 0  sales store_nbr month  \
5  02/08/2017  Features - [1 0 0][1 0 1 12]   12122.50 541.36     27.50  8.00   

  day_of_month week_of_year day_of_week dcoilwtico_interpolated  \
5         2.00        31.00        3.00                   49.28   

  family_encoded type_encoded y_pred y_pred_raw fit_time  error features  
5          16.00         2.00 442.53     442.53   494.03 -98.84        1

order:
p: 1
d: 0
q: 1

Seasonal_order:
P: 1
D: 0
Q: 1
s: 12

In [12]:
import plotly.subplots as sp
import plotly.graph_objects as go

grouped_df_family = result_df[result_df['order_and_seasonal_order'] == closest_to_zero_row['order_and_seasonal_order'].iloc[0]]
grouped_df_family

family_encodes = grouped_df_family['family_encoded'].unique()

# Define the number of family encodes to display in each row
family_encodes_per_row = 5

# Calculate the number of rows and columns required
num_rows = (len(family_encodes) + family_encodes_per_row - 1) // family_encodes_per_row
num_cols = min(len(family_encodes), family_encodes_per_row)

# Define the figure size
fig_height = 2000  # Set the desired height of the figure
fig_width = 1750  # Set the desired width of the figure

# Create subplots with shared x-axis
fig = sp.make_subplots(rows=num_rows, cols=num_cols, shared_xaxes=True)

# Iterate over the family encodes
for i, family_encoded in enumerate(family_encodes):
    # Calculate the row and column index for the current family encode
    row = (i // family_encodes_per_row) + 1
    col = (i % family_encodes_per_row) + 1
    
    # Filter the data for the current family encode
    family_df = grouped_df_family[grouped_df_family['family_encoded'] == family_encoded]
    
    # Add the trace for y_pred_raw as a line plot
    fig.add_trace(
        go.Scatter(x=family_df['date'], y=family_df['y_pred_raw'], mode='lines', name=f"y_pred_raw"),
        row=row, col=col
    )
    
    
    # Add the trace for sales as a line plot
    fig.add_trace(
        go.Scatter(x=family_df['date'], y=family_df['sales'], mode='lines', name=f"Sales", line=dict(color='red', width=1, dash='dash')),
        row=row, col=col
    )
    

    
    # Set the subplot title based on the family_encoded value
    fig.update_xaxes(title_text=f"Family Encoded: {family_encoded}", row=row, col=col)

# Update layout and axis titles
fig.update_layout(
    title="Total Sales and y_pred per Family Encoded",
    xaxis=dict(title="Date"),
    yaxis=dict(title="Value"),
    height=fig_height,  # Set the height of the figure
    width=fig_width,  # Set the width of the figure
)

# Show the plot
fig.show()


In [13]:
# Plot the grouped data using Plotly

for g in  grouped_df_family['family_encoded'].unique():
    family_df = grouped_df_family[grouped_df_family['family_encoded'] == g]
    fig = px.line(family_df, x='date', y='y_pred_raw', color='family_encoded')

    # Plot the grouped data using Plotly
    #fig = px.line(grouped_df_family, x='date', y='y_pred_raw', color='order_and_seasonal_order',  symbol='features', symbol_map={1: 'square', 0: 'star'})

    # Add a separate line plot for 'sales' with a thicker line and different color
    sales_df = family_df[['date','sales']]
    fig.add_scatter(x=sales_df['date'], y=sales_df['sales'], mode='lines',
                    name='Sales', line=dict(color='red', width=3))

    # Add labels and title to the plot
    fig.update_layout(
        title="Total Sales and y_pred over time",
        xaxis_title="Date",
        yaxis_title="Value"
    )
    fig.show()


